In [ ]:
import numpy as np
import matplotlib.pyplot as plt

Vamos definir uma função chute inicial.

In [ ]:
def psi0(x):
  return np.exp(-(x**2)/10.0)

Vamos fazer um gráfico dessa função.

In [ ]:
fig = plt.figure()
ax = fig.add_subplot()
X = np.linspace(-5, 5, 20)
ax.scatter(X, psi0(X)**2, color='blue', marker='.')
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_title('Initial')
plt.show()

Vamos agora definir uma função alvo.

In [ ]:
def func(x):
  return np.exp(-0.0025*(x**4))

Vamos ver essa função em 3D.

In [ ]:
fig_target = plt.figure()
ax = fig_target.add_subplot(111)
X = np.linspace(-5, 5, 20)
ax.scatter(X, func(X), color='green', marker='.')
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_title('Target')
plt.show()

Com isso, o que queremos fazer é criar uma função custo que da a soma das distâncias entre os y's da função alvo e os y's da função chute. Vamos minimizar o custo usando Monte Carlo.

In [ ]:
def cost1(xx):
  return abs(psi0(xx)-func(xx))

Vamos ver o que resulta se calcularmos na malha.

In [ ]:
print(cost1(X))

In [ ]:
print(X)
print(cost1(-2.36842105))

In [ ]:
def cost(xx):
  return np.linalg.norm(psi0(xx)-func(xx))

In [ ]:
cost(X)

In [ ]:
print(np.sqrt(sum([cost1(x)**2 for x in X])))

A ideia do Monte Carlo que vamos fazer é variar aleatoriamente, de acordo com uma "temperatura", os valores de y dados pela função chute e ver se o custo diminui. Aí começamos com uma temperatura alta que dá uma gaussiana centrada no ponto, mas com grandes amplitudes de deslocamento. Fazemos isso para cada um dos pontos e testamos o custo. Mas, vamos começar com a temperatura inicial alta.

In [ ]:
T0=10.0

Agora, quando a temperatura for muito baixa, a variação é pouca em torno da atual função que estamos variando. Isso deve acontecer só depois quando já tivermos uma boa solução que vamos consolidar. Então vamos definir uma temperatura final bem baixa.

In [ ]:
Tf=0.00001

Precisamos agora de uma taxa de decréscimo da temperatura, representada por um parâmetro que vai depois ser usado para um fator de decréscimo da temperatura.

In [ ]:
tau=0.01

Como temos que variar muitas vezes a função chute até achar uma que minimiza o custo o suficiente, vamos definir o número de tentativas que vamos fazer para cada temperatura antes de esfriar as variações.

In [ ]:
N=100

Agora inicializamos o que precisamos, que é Y do chute e o custo para cada ponto da malha.

In [ ]:
E=cost(X)
Y=psi0(X)
print(E)
print(Y)

Vamos inicializar a temperatura.

In [ ]:
T=T0

Enquanto não atingimos a temperatura final, vamos ficar rodando as tentativas. Então usamos um comando while.

In [ ]:
# while T>Tf:

Eu comentei porque não escrevemos tudo ainda. Aí precisamos de um comando for para repetir as tentativas.

In [ ]:
#while T>Tf:
#  for i in range(N):

O próximo passo é variar os valores de Z com uma variância, digamos, igual à temperatura.

In [ ]:
"""
while T>Tf:
  for i in range(N):
    Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
"""

Agora nós precisamos calcular o novo custo. E agora fica complicado, pois não podemos mais usar a mesma função chute de antes. Vamos definir o custo de forma que possamos calcular com o Znew. Para fazer isso, vamos dar o comando do Znew e ver se podemos definir a função custo diretamente.

In [ ]:
d=20
Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
print(Y)
print(Ynew)
#np.linalg.norm(psi0(xx,yy)-func(xx,yy))

Vemos que cada vez que repetimos o comando, Ynew muda de valores. Agora vamos ver se conseguimos definir o custo diretamente no caso do Y.

In [ ]:
Eold=np.linalg.norm(Y-func(X))
print(Eold)
print(cost(X))

Vemos que é exatamente o que deveria ser. Calculemos o novo custo dessa maneira direta.

In [ ]:
Enew=np.linalg.norm(Ynew-func(X))
print(Enew)

E vemos que o custo cresceu bastante. Já se a temperatura for baixa, como a final, o custo fica menor.

In [ ]:
T=Tf
Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
print(Y)
print(Ynew)
Enew=np.linalg.norm(Ynew-func(X))
print(Enew)

O custo ficou até um pouco menor do que o original, mas ficou bem próximo, pois a temperatura baixa não deixa o Y variar muito. Agora podemos usar essa nova forma de calcular custo no nosso algoritmo de Monte Carlo.

In [ ]:
"""
while T>Tf:
  for i in range(N):
    Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
    Enew=np.linalg.norm(Ynew-func(X))
"""

Agora precisamos fazer a parte principal do algoritmo que é um jogo.

In [ ]:
"""
while T>Tf:
  for i in range(N):
    Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
    Enew=np.linalg.norm(Ynew-func(X))
    if Enew < E or np.random.rand() < np.exp(-(Enew - E)/T):
"""

Essa linha de comando agora vai fazer o cálculo de um número menor que 1, que é np.random.rand(). Vamos ver que é menor que um.

In [ ]:
[np.random.rand() for i in range(10)]

Essa é a nossa moeda. Aí calculamos um fator de Boltzmann, np.exp(-(Enew - E)/T), que é ou menor que 1 ou maior que 1, dependendo se o custo aumenta ou diminui. Se o custo, por exemplo, diminuir, então a linha de comando já vai para o próximo passo do algoritmo. Caso o custo aumente ou fique igual, aí vamos ver o que a moeda dá e comparar com o fator de Boltzmann. Caso o número aleatório seja menor do que o fator de Boltzmann, fazemos o próximo passo. E esse próximo passo é aceitar a mudança. Se esse if falhar, no entanto, aí nós vamos para a próxima rodada do jogo e continuamos com o loop.

In [ ]:
"""
while T>Tf:
  for i in range(N):
    Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
    Enew=np.linalg.norm(Ynew-func(X))
    if Enew < E or np.random.rand() < np.exp(-(Enew - E)/T):
      if Enew <E0:
        Z=Znew
        E=Enew
"""

O ponto é que agora vamos sair do loop e ter atualizado algumas vezes o valor de Y durante essas N rodadas com a temperatura T. Antes de continuar o loop do while, precisamos diminuir um pouco a temperatura.

In [ ]:
"""
while T>Tf:
  for i in range(N):
    Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
    Enew=np.linalg.norm(Ynew-func(X))
    if Enew < E or np.random.rand() < np.exp(-(Enew - E)/T):
      if Enew <E0:
        Z=Znew
        E=Enew
        print(E)
  T = T * np.exp(-tau)
"""

Vemos que multiplicamos a temperatura agora por um fator menor que 1 e isso é feito depois de cada rodada de N tentativas jogando a moeda. Vamos ver o que dá.

In [ ]:
type(Y)
np.shape(Y)

In [ ]:
d=10
X = np.linspace(-4, 4, d)
T=0.01
Tf=0.00001
Y=psi0(X)
N=100
tau=0.001
E=np.linalg.norm(Y-func(X))
print(E)
Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
Enew=np.linalg.norm(Ynew-func(X))
print(Enew)
print(np.exp(-(Enew - E)/T))
print(np.random.rand())

In [ ]:
d=5
X = np.linspace(-2, 2, d)
T=0.06
Tf=0.0000001
Y=psi0(X)
E=np.linalg.norm(Y-func(X))
E0=E
N=100
tau=0.001
while T>Tf:
  for i in range(N):
    Ynew=np.array([Y[k]+np.random.normal(0,np.sqrt(T)) for k in range(d)])
    Enew=np.linalg.norm(Ynew-func(X))
    if Enew < E or np.random.rand() < np.exp(-(Enew - E)/T):
      if Enew <E0:
        Y=Ynew
        E=Enew
        print(E)
  T = T * np.exp(-tau)

Vejamos o custo novo.

In [ ]:
print(E)

In [ ]:
cost(X)

In [ ]:
fig = plt.figure()
ax = fig.add_subplot()
X = np.linspace(-2, 2, d)
ax.scatter(X, Y, color='blue', marker='.')
ax.scatter(X, func(X), color='red', marker='.')
ax.set_xlabel('x')
ax.set_ylabel('y')
plt.show()

In [ ]:
print(Y[2])

In [ ]:
print(func(X)[2])